# Imports

In [11]:
%%capture
# установка gradio для написания веб интерефейса
# установка transformers для использования языковых моделей с платформы HF

!pip install gradio transformers

In [12]:
import random
import time
from typing import List, Dict, Tuple, Union
from IPython import display

import gradio as gr
import torch
import transformers

In [13]:
# версии библиотек
!pip list | grep -P "torch|transformers|gradio"

gradio                           4.4.1
gradio_client                    0.7.0
torch                            2.1.0+cu118
torchaudio                       2.1.0+cu118
torchdata                        0.7.0
torchsummary                     1.5.1
torchtext                        0.16.0
torchvision                      0.16.0+cu118
transformers                     4.35.2


# Tokenizer and Model

**Инициализация модели**  
Страница модели  
https://huggingface.co/ai-forever/rugpt3medium_based_on_gpt2

In [14]:
from transformers import pipeline
from transformers import AutoTokenizer, AutoModelForCausalLM, GenerationConfig

# # инициализация через pipeline
# model_name = "ai-forever/rugpt3medium_based_on_gpt2"
# pipe = pipeline("text-generation", model=model_name)
# sample = pipeline('test test', pad_token_id=generator.tokenizer.eos_token_id)

model_name = "ai-forever/rugpt3medium_based_on_gpt2"
model = AutoModelForCausalLM.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)
tokenizer.pad_token_id = tokenizer.eos_token_id

DEVICE = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model = model.to(DEVICE)

Генерация текста

In [15]:
%%time

# токенизация текста в индексы токенов и маски внимания
text_promt = 'меня засосала опасная трясина '
inputs = tokenizer(text_promt, return_tensors="pt").to(DEVICE)

# конфиг словарь для генерации текста
gen_config_dict = dict(
                    do_sample=True,  # делать ли случайное семплирование с параметрами ниже (если False то выскочит предупреждение)
                    max_new_tokens=30,  # сколько максимум новых токенов надо генерировать
                    top_k=50,  # семплировать только из top_k самых вероятных токенов
                    top_p=0.9,  # семплировать только из токенов сумма вероятностей которых не больше top_p
                    temperature=2.0,  # температура для софтмакса
                    num_beams=3,  # параметр алгоритма Beam search
                    repetition_penalty=2.0,  # штраф за то что модель повторяется
                    pad_token_id=tokenizer.pad_token_id,  # установить токен pad чтобы не было предупреждения
                    )
# конфиг для генерации текста из словаря
generation_config = GenerationConfig(**gen_config_dict)

# генерация текста (индексы токенов)
output = model.generate(**inputs, generation_config=generation_config)

# сопостовление идексам токенов слов из словаря токенайзера
generated_text = tokenizer.decode(output[0], skip_special_tokens=False)

# удаление исходного промта из ответа потому что он тоже возвращается
generated_text = generated_text[len(text_promt):]
generated_text

CPU times: user 11.4 s, sys: 27.2 ms, total: 11.5 s
Wall time: 15.6 s


'\nГрязь, гниль, вонь, вонище, хлябь, тухлятина, плесень, чавка'

Функция для генерации

In [16]:
# функция принимает текстовый запрос и словарь параметров генерации
def generate_text(text_promt: str, gen_config_dict: Dict[str, Union[float, int]]) -> str:
    inputs = tokenizer(text_promt, return_tensors="pt").to(DEVICE)
    generation_config = GenerationConfig(**gen_config_dict)
    output = model.generate(**inputs, pad_token_id=tokenizer.eos_token_id, generation_config=generation_config)
    generated_text = tokenizer.decode(output[0], skip_special_tokens=True)
    generated_text = generated_text[len(text_promt):]
    return generated_text


# конфиг словарь для генерации текста
gen_config_dict = dict(
                    do_sample=True,  # делать ли случайное семплирование с параметрами ниже (если False то выскочит предупреждение)
                    max_new_tokens=20,  # сколько максимум новых токенов надо генерировать
                    top_k=50,  # семплировать только из top_k самых вероятных токенов
                    top_p=0.9,  # семплировать только из токенов сумма вероятностей которых не больше top_p
                    temperature=2.0,  # температура для софтмакса
                    num_beams=3,  # параметр алгоритма Beam search
                    repetition_penalty=2.0,  # штраф за то что модель повторяется
                    pad_token_id=tokenizer.pad_token_id,  # установить токен pad чтобы не было предупреждения
                    )


text_promt = 'в небесной канцелярии выходной'
generated_text = generate_text(text_promt, gen_config_dict)
generated_text

', и только после этого можно заниматься этим вопросом.  Но это уже совсем другие истории, которые могут'

# Gradio App

## Новый интерфейс Чат-бота

Вариант с системным промтом и разными входными аргументами и настройками

In [17]:
import gradio as gr

# функция будет вызыватся при нажатии на Enter в окошке вовода текста
# кроме обычных аргументов - сообщения пользователя и истории - принимает еще параметры для конфига генерации
def generate(message, history, *components):
    # print(system_promt)
    # обновление словаря новыми агрументами и создание конфига генерации текста
    gen_config.update(dict(zip(gen_config.keys(), components)))
    gen_config['top_k'] = int(gen_config['top_k'])
    gen_config['num_beams'] = int(gen_config['num_beams'])
    generation_config = GenerationConfig(**gen_config)

    # добавить системный промт в начало запроса и сгенерировать текст
    promt = message
    inputs = tokenizer(promt, return_tensors="pt").to(DEVICE)
    output = model.generate(**inputs, generation_config=generation_config, pad_token_id=tokenizer.eos_token_id)
    generated_text = tokenizer.decode(output[0], skip_special_tokens=True)
    generated_text = generated_text[len(promt):]
    # имитация набора сообщения чат-ботом (посимвольня генерация через yield в цикле)
    for i in range(len(generated_text)):
        time.sleep(0.05)  # задержка с которой бот вводит текст
        yield generated_text[:i+1]

# словарь для конфига генерации текста
gen_config = dict(
            do_sample=False,
            max_length=60,
            top_k=50,
            top_p=0.9,
            temperature=2.0,
            num_beams=3,
            repetition_penalty=2.0,
            )


# компоненты настройки конфига генерации текста
components = [
    gr.Checkbox(label="do_sample", value=gen_config["do_sample"]),
    gr.Slider(label="max_length", value=gen_config["max_length"], minimum=1, maximum=300, step=10),
    gr.Number(label="top_k", value=gen_config["top_k"], minimum=0, maximum=50, step=10),
    gr.Number(label="top_p", value=gen_config["top_p"], minimum=0, maximum=1, step=0.1),
    gr.Number(label="temperature", value=gen_config["temperature"], minimum=0, maximum=10, step=0.1),
    gr.Number(label="num_beams", value=gen_config["num_beams"], minimum=0, maximum=5, step=1),
    gr.Number(label="repetition_penalty", value=gen_config["repetition_penalty"], minimum=0, maximum=5, step=0.1),
        ]

# при нажатии Enter в чате будет вызыватся функция generate
interface = gr.ChatInterface(
            generate,
            chatbot=gr.Chatbot(height=300),  # вход для функции generate: message
            textbox=gr.Textbox(placeholder="Задайте любой вопрос", container=False, scale=2),  # выходной бокс для текста

            # дополнительные входы для функции generate (*components)
            additional_inputs=components,

            # настройки оформления
            title="Чат-бот T10",  # название страницы
            description="Окно переписки с ботом",  # описание окошка переписки
            theme="Glass",  # темы: Glass, Monochrome, Soft
            # examples=["Hello", "Am I cool?", "Are tomatoes vegetables?"],  # примеры должны быть множественными если аргументов много
            # cache_examples=True,  # кешировать примеры

            # дполнительные кнопки (если не нужна какая либо кнопка ставим None)
            submit_btn='Отправить',
            retry_btn='Повторить вопрос',
            undo_btn="Удалить предыдущий вопрос",
            clear_btn="Очистить историю",
)

# запуск приложения
interface.queue().launch(debug=True)

Setting queue=True in a Colab notebook requires sharing enabled. Setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
Running on public URL: https://82df78dd1728af38f1.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)


/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:381: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `2.0` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`. This was detected when initializing the generation config instance, which means the corresponding file may hold incorrect parameterization and should be fixed.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:386: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`. This was detected when initializing the generation config instance, which means the corresponding file may hold incorrect parameterization and should be fixed.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuratio

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7861 <> https://82df78dd1728af38f1.gradio.live
